In [1]:
import json
import pandas as pd
import plotly.graph_objects as go
import matplotlib as mpl
import numpy as np
import matplotlib.pyplot as plt

In [67]:
df = pd.read_excel('data.xlsx')# read data from the file
names = ['Shandong', 'Jiangsu', 'Shanghai', 'Henan']#choose the 4 near province of China 
df = df.query('provinceEnglishName in @names')# choose these province from the whole map
df.columns = ['province', 'provinceEnglishName','number']# set the column
print(df) # Store the data required for each drawing

splits = 10000# number of individual colours to use in full version 
halfway = int(splits/2)# number of individual colours to use in truncated version

colour_values = mpl.cm.Reds(np.linspace(0, 1, splits))# list of rgb colours for full version. Returns num evenly spaced samples, calculated over the interval [start, stop]
trunc_colours = colour_values[0:halfway,:]# row 0 to halfway
#print(trunc_colours)
trunc_index=np.linspace(0,1,halfway)# splite the 0-1 to get the index of color
#print(trunc_index)
trunc_cmap=[]
for index,value in zip(trunc_index,trunc_colours):# use index and value to iterate in trunc_index and trunc_coloues.create the color which correspond to the index
  trunc_cmap.append([index,'rgb({0:d},{1:d},{2:d})'.format(int(value[0]*255),int(value[1]*255),int(value[2]*255))])#Re match color and index. 

full_colours = colour_values[:,:] # all rows, all columns
full_index=np.linspace(0,1,splits)
full_cmap = []
for index,value in zip(full_index,full_colours):# full colour range 
  full_cmap.append([index,'rgb({0:d},{1:d},{2:d})'.format(int(value[0]*255),int(value[1]*255),int(value[2]*255))])#Convert the following integers into strings and splice them into RGB strings
# [0.0, 'rgb(255,245,240)']
#print(full_cmap)

with open('china.json', encoding='utf-8') as response:#load the json file
    geojson = json.load(response)


def getFigure(range1=None):
    if range1 is None:
        zmin = 0# color show from 0
        zmax = df['number'].max() # zmax is the most biggest number in 4 provinces
        colors = trunc_cmap# what range of colour to use 
    else:
        zmin = 0
        zmax = df['number'].max()*2 # double range of color
        colors = full_cmap

    fig = go.Figure( 
        go.Choropleth(# use the go library of plotly. using a graph object.  Draw the figure
        locations=df['province'],# Spatial coordinates
        z=df['number'],#Data to be color-coded
        zmin=zmin,#Sets the lower bound of the color domain. 
        zmax=zmax,#Sets the upper bound of the color domain. 
        geojson=geojson,# layout json
        featureidkey='properties.name',#use this key in the json file to corredpond to the name in 'locations'
        colorscale=colors, # use the color we set before
        #locationmode='geojson-id',# set of locations match entries in `locations`
        colorbar_len=0.6,# the length of colorbar
        
    ))

    fig.update_geos(fitbounds="locations",)#Determines if this subplot's view settings are auto-computed to fit trace data
    fig.update_geos(showframe=False,# Set the display details, and do not display the parts irrelevant to the experiment
                          showcoastlines=False,
                          showcountries=False,
                          showland=False,
                          showlakes=False,
    )
    
    fig.update_traces(colorbar_orientation='h',  selector=dict(type='choropleth'))#colorbar is horiziontial
    fig.update_traces(marker_line_color='black', selector=dict(type='choropleth'))# board line's colour


    return fig


figure = getFigure()# draw the narrow range color
figure.show()
figure = getFigure(1)# draw the full range color
figure.show()

   province provinceEnglishName  number
7       山东省            Shandong    3000
8       江苏省             Jiangsu    2900
14      河南省               Henan    2800
16      上海市            Shanghai    3000
